This script can be used for the three protein separation chromatography modeling exercise.
<br>
The user can change the input parameters found in this script to explore their affect on the simulated separation process.

Necessary packages and scripts are imported here.

In [1]:
import time
import pandas as pd
from pathlib import Path
import sys, os
import CADET_sim
import create_ms
import evaluate_sim
import plotting

sys.path.append('/Users/angelamoser/Documents/05_Academic/RPI/07_Chromatography_Class/modeling_assignment_code')

Paste in the CADET bin path

In [2]:
cadet_bin_path = Path() / r'/Users/angelamoser/opt/anaconda3/envs/CADET-env/bin'

First set the column parameters

In [3]:
col_id = 1 # [cm], Column diameter
col_length = 20 # [cm], Column length   
Ee = 0.4
Ep = 0.9
particle_diameter = 85 # [um]
pore_radius = 32 # [nm]
ionic_cap_mM = 91 # [mol / L column]

Next enter the feed concentrations in mg/mL
component 1 is impurity A
component 2 is the product
component 3 is impurity B

In [4]:
comp1_conc = 0.4
comp2_conc = 2
comp3_conc = 0.2

Enter the feed component molecular weights in kDa

In [5]:
MW_1 = 36
MW_2 = 20
MW_3 = 9

Enter the isotherm parameters for each component

In [6]:
Keq_1 = 0.0329
steric_factor_1 = 25.5
characteristic_charge_1 = 5.2

Keq_2 = 0.0037
steric_factor_2 = 15.2
characteristic_charge_2 = 5.6

Keq_3 = 0.016
steric_factor_3 = 17
characteristic_charge_3 = 3.3

Enter the residence time for all steps in the process in minutes

In [7]:
residence_time = 3

Next set the salt concentrations for each step in the process in mM.
<br><br>
The process has 5 steps:
<br><br>
load - where the feed solution is loaded onto the column in binding (low salt) conditions
<br>
wash - wash buffer, typically at similar conditions to the load but containing no protein, is flowed through the column to  wash out any remaining unbound feed solution
<br>
elution step 1 - the lowest salt elution step. This step should wash out as much of the impurities that bind more weakly than the target protein as possible, without eluting the target protein.
<br>
elution step 2 - the second salt step is where the product should elute, with as little of the more strongly binding impurities as possible
<br>
elution step 3 - this step is used to wash out any of the remaining strong binding proteins from the column
<br><br>
salt is used as the mobile phase modifier in this case because we are simulating ion exchange chromatography

In [8]:
load_salt = 50
wash_salt = 50
step1_salt = 200
step2_salt = 400
step3_salt = 600

Enter the length of each step in the process in column volumes
A typical wash or elution step length could be around 5 column volumes, but it could be less if elution happens quickly or more if the peak is very broad

In [9]:
load_CV = 5
wash_CV = 5
step1_CV = 5
step2_CV = 5
step3_CV = 5

Finally, enter the concentration of the product species that you would like to use to determine where fraction collection begins and ends. 

This can be used to modulate the purity and yield of the process, but there is always a trade off between the two. For example, choosing to start fraction collection at a higher concentration may increase purity as less of the overlapping peak is collected, but this will decrease yield.

In [10]:
cutoff = 0.5

Run the following section to add all the inputs to the model

In [11]:
run_conditions = {}
run_conditions['cadet_bin_path'] = cadet_bin_path
           
run_conditions['load salt [mM]'] = load_salt
run_conditions['wash salt [mM]'] = wash_salt
run_conditions['step 1 salt [mM]'] = step1_salt
run_conditions['step 2 salt [mM]'] = step2_salt
run_conditions['step 3 salt [mM]'] = step3_salt
    
run_conditions['load CVs'] = load_CV
run_conditions['wash CVs'] = wash_CV
run_conditions['step 1 CVs'] = step1_CV
run_conditions['step 2 CVs'] = step2_CV
run_conditions['step 3 CVs'] = step3_CV
    
run_conditions['residence time [min]'] = residence_time
            
run_conditions['impurity A concentration [mg/mL]'] = comp1_conc
run_conditions['product concentration [mg/mL]'] = comp2_conc
run_conditions['impurity B concentration [mg/mL]'] = comp3_conc
   
run_conditions['impurity A MW'] = MW_1
run_conditions['product MW'] = MW_2
run_conditions['impurity B MW'] = MW_3

run_conditions['column ID [cm]'] = col_id
run_conditions['column length [cm]'] = col_length  
run_conditions['Ee'] = Ee
run_conditions['Ep'] = Ep
run_conditions['particle diameter [um]'] = particle_diameter
run_conditions['pore radius [nm]'] = pore_radius
run_conditions['ionic capacity [mol / L column]'] = ionic_cap_mM
    
run_conditions['Keq 1'] = Keq_1
run_conditions['steric factor 1'] = steric_factor_1
run_conditions['characteristic charge 1'] = characteristic_charge_1
    
run_conditions['Keq 2'] = Keq_2
run_conditions['steric factor 2'] = steric_factor_2
run_conditions['characteristic charge 2'] = characteristic_charge_2 
    
run_conditions['Keq 3'] = Keq_3
run_conditions['steric factor 3'] = steric_factor_3
run_conditions['characteristic charge 3'] = characteristic_charge_3

run_conditions['collection cutoff [mg/mL]'] = cutoff

ms = create_ms.create_ms(run_conditions)

Run the simulation and generate the output table and plot.
The simulation should take around 1 minute to run.

In [12]:
tic = time.perf_counter()
sim_solution = CADET_sim.run_cadet_sim(ms)

# convert time from [sec] to [min], create a [CV] column
sim_solution = process_simulation_data(sim_solution, ms) 
              
# calculates pool volume, yield, etc. and saves results as a dictionary
results = evaluate_sim.evaluate_simulation(sim_solution, ms)

print('Forward Simulation Results:')    
# Convert from list of dicts to DataFrame
results = pd.DataFrame(results)
# Print results table to console
with pd.option_context('display.max_rows', 5,
                       'display.max_columns', None,
                       'display.precision', 3,
                       ):
    display(results)
             
# Generate plots
plot = plotting.generate_plot(sim_solution, ms)  
               
# end timer and print run time
toc = time.perf_counter()
print(f'\n Completed in {toc - tic:.4f} seconds')


Simulation Running!

CompletedProcess(args=['/Users/angelamoser/opt/anaconda3/envs/CADET-env/bin/cadet-cli', 'model.h5'], returncode=2, stdout=b'', stderr=b'IO ERROR: Field "IS_KINETIC" does not exist in group /input/model/unit_002/adsorption\n')


Exception: Simulation failed